## Installing Scikit-mobility on Colab


In [1]:
!apt-get install -qq curl g++ make
!curl -L http://download.osgeo.org/libspatialindex/spatialindex-src-1.8.5.tar.gz | tar xz
import os
os.chdir('spatialindex-src-1.8.5')
!./configure
!make
!make install
!pip install rtree
!ldconfig
!pip install scikit-mobility

  % Total    % Received % Xferd  Average Speed   Time    Time     Time  Current
                                 Dload  Upload   Total   Spent    Left  Speed
100  556k  100  556k    0     0   706k      0 --:--:-- --:--:-- --:--:--  705k
checking build system type... x86_64-unknown-linux-gnu
checking for g++... g++
checking whether the C++ compiler works... yes
checking for C++ compiler default output file name... a.out
checking for suffix of executables... 
checking whether we are cross compiling... no
checking for suffix of object files... o
checking whether we are using the GNU C++ compiler... yes
checking whether g++ accepts -g... yes
checking how to run the C++ preprocessor... g++ -E
checking for a BSD-compatible install... /usr/bin/install -c
checking whether ln -s works... yes
checking whether make sets $(MAKE)... yes
checking host system type... x86_64-unknown-linux-gnu
checking how to print strings... printf
checking for gcc... gcc
checking whether we are using the GNU C compil

## Mobility Data Analysis

In [1]:
import skmob
from skmob.preprocessing import detection, clustering, filtering, compression
import pandas as pd
import folium
import folium.plugins as fp

In [2]:
#!pip install pandas==1.2.4

In [3]:
# With pandas version > 1.2.5, some of the functionalities don't work so we need to downgrade to 1.2.4
pd.__version__

'1.2.4'

In [4]:
df = pd.read_csv('/content/drive/MyDrive/SIR1/SUMO/nis-trajectories.csv')
df.head()

timestep_time  vehicle_angle  vehicle_id   vehicle_lane  vehicle_pos  \
0            0.0     177.039064         0.0  115561258#2_0     5.100000   
1            1.0     177.039064         0.0  115561258#2_0     6.814126   
2            1.0     281.601701         1.0   -140789746_0     5.100000   
3            2.0     177.039064         0.0  115561258#2_0    11.050417   
4            2.0     281.601701         1.0   -140789746_0     7.092834   

   vehicle_slope  vehicle_speed     vehicle_type  vehicle_x  vehicle_y  
0            0.0       0.000000  DEFAULT_VEHTYPE  21.923416  43.327400  
1            0.0       1.714126  DEFAULT_VEHTYPE  21.923417  43.327385  
2            0.0       0.000000  DEFAULT_VEHTYPE  21.940220  43.334393  
3            0.0       4.236291  DEFAULT_VEHTYPE  21.923419  43.327350  
4            0.0       1.992834  DEFAULT_VEHTYPE  21.940199  43.334397

In [5]:
num_of_unique_vehicles = df['vehicle_id'].nunique()
num_of_unique_vehicles

3600

In [6]:
df.dropna()

timestep_time  vehicle_angle  vehicle_id    vehicle_lane  vehicle_pos  \
0                 0.0     177.039064         0.0   115561258#2_0     5.100000   
1                 1.0     177.039064         0.0   115561258#2_0     6.814126   
2                 1.0     281.601701         1.0    -140789746_0     5.100000   
3                 2.0     177.039064         0.0   115561258#2_0    11.050417   
4                 2.0     281.601701         1.0    -140789746_0     7.092834   
...               ...            ...         ...             ...          ...   
787070         4144.0     196.993066      3370.0  -417316208#1_0    46.637322   
787071         4145.0      16.999921      3370.0   417316208#1_0     5.071557   
787072         4146.0      16.999921      3370.0   417316208#1_0    15.789927   
787073         4147.0      23.455732      3370.0   417316208#1_0    28.431887   
787074         4148.0      26.991127      3370.0   417316208#1_0    42.600439   

        vehicle_slope  vehicle_speed     vehicle_type  vehicle_x  vehicle_y  
0                 0.0       0.000000  DEFAULT_VEHTYPE  21.923416  43.327400  
1                 0.0       1.714126  DEFAULT_VEHTYPE  21.923417  43.327385  
2                 0.0       0.000000  DEFAULT_VEHTYPE  21.940220  43.334393  
3                 0.0       4.236291  DEFAULT_VEHTYPE  21.923419  43.327350  
4                 0.0       1.992834  DEFAULT_VEHTYPE  21.940199  43.334397  
...               ...            ...              ...        ...        ...  
787070            0.0       6.866562  DEFAULT_VEHTYPE  21.926543  43.308171  
787071            0.0       9.304235  DEFAULT_VEHTYPE  21.926584  43.308168  
787072            0.0      10.718369  DEFAULT_VEHTYPE  21.926616  43.308241  
787073            0.0      12.641960  DEFAULT_VEHTYPE  21.926659  43.308326  
787074            0.0      14.168552  DEFAULT_VEHTYPE  21.926723  43.308416  

[787075 rows x 10 columns]

In [ ]:
# Maximum vehicle speed from df
df['vehicle_speed'].max()

37.322186

In [7]:
tdf = skmob.TrajDataFrame(df, latitude='vehicle_y', longitude='vehicle_x', datetime='timestep_time', user_id='vehicle_id', timestamp=True)
tdf.head()

datetime  vehicle_angle  uid   vehicle_lane  vehicle_pos  \
0 1970-01-01 00:00:00     177.039064  0.0  115561258#2_0     5.100000   
1 1970-01-01 00:00:01     177.039064  0.0  115561258#2_0     6.814126   
2 1970-01-01 00:00:01     281.601701  1.0   -140789746_0     5.100000   
3 1970-01-01 00:00:02     177.039064  0.0  115561258#2_0    11.050417   
4 1970-01-01 00:00:02     281.601701  1.0   -140789746_0     7.092834   

   vehicle_slope  vehicle_speed     vehicle_type        lng        lat  
0            0.0       0.000000  DEFAULT_VEHTYPE  21.923416  43.327400  
1            0.0       1.714126  DEFAULT_VEHTYPE  21.923417  43.327385  
2            0.0       0.000000  DEFAULT_VEHTYPE  21.940220  43.334393  
3            0.0       4.236291  DEFAULT_VEHTYPE  21.923419  43.327350  
4            0.0       1.992834  DEFAULT_VEHTYPE  21.940199  43.334397

In [8]:
m = tdf.plot_trajectory(zoom=14, max_users=30)
m

/usr/local/lib/python3.7/dist-packages/skmob/core/trajectorydataframe.py:571: UserWarning: If necessary, trajectories will be down-sampled to have at most `max_points` points. To avoid this, specify `max_points=None`.
  start_end_markers=start_end_markers, control_scale=control_scale)


In [9]:
pois = pd.read_csv('/content/drive/MyDrive/SIR1/SUMO/OSM/serbia-pois.osm.csv', sep="|")
pois.head()

ID                NAME CATEGORY SUBCATEGORY        LON  \
0  node/26862545            Бељаница  TOURISM        PEAK  21.699497   
1  node/26862552        Бесна кобила  TOURISM        PEAK  22.230507   
2  node/26862747            Црни врх  TOURISM        PEAK  22.222173   
3  node/26863071  Гулијанска планина  TOURISM        PEAK  22.264741   
4  node/26863270        Јанков камен  TOURISM        PEAK  20.276493   

         LAT  SRID                                            WKT  \
0  44.111776  4326                  POINT (21.6994972 44.1117761)   
1  42.529501  4326                  POINT (22.2305074 42.5295008)   
2  44.226415  4326                   POINT (22.2221733 44.226415)   
3  43.326753  4326          POINT (22.2647406 43.326753100000005)   
4  43.339294  4326  POINT (20.276493300000002 43.339294300000006)   

  INTERNATIONAL_NAME STREET  ... DESCRIPTION WEBSITE LAST_UPDATE OPERATOR  \
0                NaN    NaN  ...         NaN     NaN         NaN      NaN   
1                NaN    NaN  ...         NaN     NaN         NaN      NaN   
2                NaN    NaN  ...         NaN     NaN         NaN      NaN   
3                NaN    NaN  ...         NaN     NaN         NaN      NaN   
4                NaN    NaN  ...         NaN     NaN         NaN      NaN   

  POSTCODE COUNTRY  FAX IMAGE HOUSENUMBER  \
0      NaN     NaN  NaN   NaN         NaN   
1      NaN     NaN  NaN   NaN         NaN   
2      NaN     NaN  NaN   NaN         NaN   
3      NaN     NaN  NaN   NaN         NaN   
4      NaN     NaN  NaN   NaN         NaN   

                                          OTHER_TAGS  
0  {"natural":"peak","name:sr-Latn":"Beljanica","...  
1  {"natural":"peak","name:sr-Latn":"Besna kobila...  
2  {"natural":"peak","name:sr-Latn":"Crni vrh","n...  
3  {"name":"Гулијанска планина","natural":"peak",...  
4  {"natural":"peak","name:sr-Latn":"Jankov kamen...  

[5 rows x 26 columns]

In [10]:
len(pois)

44702

In [11]:
# POIs filtering
nis_pois = pois[(pois['LAT']<43.393380) & (pois['LAT']>43.243670) & (pois['LON']<22.093517) & (pois['LON']>21.712435)]
nis_pois = nis_pois.reset_index()
nis_pois

index                 ID                           NAME       CATEGORY  \
0        38     node/100890898                            Ниш    SETTLEMENTS   
1       355     node/408157341                      Белотинце      TRANSPORT   
2       528     node/453435264                          Бубањ     AUTOMOTIVE   
3       529     node/453435272  Главна полицијска станица Ниш  PUBLICSERVICE   
4       530     node/453435274                 Ватрогасни дом  PUBLICSERVICE   
...     ...                ...                            ...            ...   
1381  44686  relation/12885650     Електронска индустрија Ниш        LANDUSE   
1382  44687  relation/12890686                      Парк Чаир        LANDUSE   
1383  44688  relation/12897614                    Учитељ Таса      EDUCATION   
1384  44689  relation/12903328                  ФК Железничар          SPORT   
1385  44691  relation/13010299                  Istanbul Gate        TOURISM   

      SUBCATEGORY        LON        LAT  SRID  \
0            CITY  21.895923  43.321130  4326   
1         STATION  21.841845  43.264651  4326   
2         PARKING  21.868779  43.307362  4326   
3          POLICE  21.896653  43.319389  4326   
4     FIRESTATION  21.909235  43.322329  4326   
...           ...        ...        ...   ...   
1381   INDUSTRIAL  21.948675  43.305255  4326   
1382         PARK  21.905083  43.315091  4326   
1383       SCHOOL  21.897364  43.315041  4326   
1384      STADIUM  21.906023  43.312929  4326   
1385         GATE  21.895341  43.323319  4326   

                                                    WKT INTERNATIONAL_NAME  \
0         POINT (21.895923200000002 43.321130100000005)                NaN   
1                         POINT (21.8418449 43.2646506)                NaN   
2         POINT (21.868778600000002 43.307361500000006)                NaN   
3                         POINT (21.8966531 43.3193895)                NaN   
4                 POINT (21.9092351 43.322328600000006)                NaN   
...                                                 ...                ...   
1381  POLYGON ((21.9468955 43.303627000000006, 21.94...                NaN   
1382  POLYGON ((21.903287900000002 43.31336510000000...                NaN   
1383  POLYGON ((21.896669300000003 43.3149504, 21.89...                NaN   
1384  POLYGON ((21.9053083 43.3125413, 21.9050835 43...                NaN   
1385  POLYGON ((21.8953211 43.323257500000004, 21.89...                NaN   

      ... DESCRIPTION WEBSITE LAST_UPDATE OPERATOR POSTCODE COUNTRY  FAX  \
0     ...         NaN     NaN         NaN      NaN      NaN     NaN  NaN   
1     ...         NaN     NaN         NaN      NaN      NaN     NaN  NaN   
2     ...         NaN     NaN         NaN      NaN      NaN     NaN  NaN   
3     ...         NaN     NaN         NaN      NaN      NaN     NaN  NaN   
4     ...         NaN     NaN         NaN      NaN      NaN     NaN  NaN   
...   ...         ...     ...         ...      ...      ...     ...  ...   
1381  ...         NaN     NaN         NaN      NaN      NaN     NaN  NaN   
1382  ...         NaN     NaN         NaN      NaN      NaN     NaN  NaN   
1383  ...         NaN     NaN         NaN      NaN      NaN     NaN  NaN   
1384  ...         NaN     NaN         NaN      NaN      NaN     NaN  NaN   
1385  ...         NaN     NaN         NaN      NaN      NaN     NaN  NaN   

     IMAGE HOUSENUMBER                                         OTHER_TAGS  
0      NaN         NaN  {"name:sl":"Niš","name:sr":"Ниш","name:sq":"Ni...  
1      NaN         NaN  {"name":"Белотинце","railway":"station","name:...  
2      NaN         NaN  {"name":"Бубањ","name:sl":"Bubanj","name:sr":"...  
3      NaN         NaN  {"name":"Главна полицијска станица Ниш","name:...  
4      NaN          56  {"amenity":"fire_station","name:sr-Latn":"Vatr...  
...    ...         ...                                                ...  
1381   NaN         NaN  {"landuse":"industrial","name":"Електронска ин... 

In [12]:
map = folium.Map(location=[43.321130, 21.895923], tiles='Stamen Terrain', zoom_start=14)
marker_cluster = fp.MarkerCluster().add_to(map)

for point in range(0, len(nis_pois)):
    folium.Marker([nis_pois['LAT'][point], nis_pois['LON'][point]], popup=nis_pois['NAME'][point], icon=folium.Icon(color='darkblue', icon_color='white', icon='male', angle=0, prefix='fa')).add_to(marker_cluster)
map

In [13]:
map_with_traj = tdf.plot_trajectory(map_f=map, zoom=14, max_users=50)
map_with_traj

/usr/local/lib/python3.7/dist-packages/skmob/core/trajectorydataframe.py:571: UserWarning: If necessary, trajectories will be down-sampled to have at most `max_points` points. To avoid this, specify `max_points=None`.
  start_end_markers=start_end_markers, control_scale=control_scale)


### Preprocesing

In [14]:
# Trajectory filtering
ftdf = filtering.filter(tdf, max_speed_kmh=400.)
n_deleted_points = len(tdf) - len(ftdf)
print(n_deleted_points)

1


In [15]:
# Trajectory compression
ctdf = compression.compress(tdf, spatial_radius_km=0.2)
print('Points of the original trajectory:\t%s'%len(tdf))
print('Points of the compressed trajectory:\t%s'%len(ctdf))

Points of the original trajectory:	787076
Points of the compressed trajectory:	49930


### Measures

In [16]:
from skmob.measures.collective import visits_per_location
vl_df = visits_per_location(tdf)
print(vl_df.head)

<bound method NDFrame.head of               lat        lng  n_visits
0       43.329536  21.925258      1927
1       43.329507  21.925259      1660
2       43.329339  21.921755      1621
3       43.329852  21.937329      1584
4       43.329746  21.937018      1584
...           ...        ...       ...
527951  43.319600  21.928991         1
527952  43.319600  21.925215         1
527953  43.319600  21.920319         1
527954  43.319600  21.920130         1
527955  43.344510  21.867855         1

[527956 rows x 3 columns]>


In [17]:
vl_df_top10 = vl_df.head(10)
most_visits_map = folium.Map(location=[vl_df_top10.lat.mean(), vl_df_top10.lng.mean()], tiles='Stamen Terrain', zoom_start=14, control_scale=True)

for index, location_info in vl_df_top10.iterrows():
    folium.Marker([location_info["lat"], location_info["lng"]]).add_to(most_visits_map)


In [18]:
most_visits_map

In [19]:
from skmob.measures.individual import frequency_rank
fr_df = frequency_rank(tdf)
print(fr_df.head())

100%|██████████| 3600/3600 [00:24<00:00, 147.64it/s]

             lat        lng  frequency_rank
uid                                        
0.0 0  43.317005  21.927240               1
    1  43.326498  21.925260               2
    2  43.326038  21.925309               3
    3  43.325838  21.925343               4
    4  43.325647  21.925381               5


In [20]:
from skmob.measures.individual import maximum_distance
md_df = maximum_distance(tdf)
print(md_df.head())

100%|██████████| 3600/3600 [00:22<00:00, 156.85it/s]

   uid  maximum_distance
0  0.0          0.030165
1  1.0          0.025886
2  2.0          0.060576
3  3.0          0.064220
4  4.0          0.033534


In [21]:
md_df.sort_values('maximum_distance', ascending=False).head()

uid  maximum_distance
724    724.0          0.081768
2864  2864.0          0.080884
969    969.0          0.080773
442    442.0          0.079619
298    298.0          0.079279

In [22]:
max_dist_traj = tdf.loc[tdf['uid']==724]
len(max_dist_traj)
max_dist_traj.head()

datetime  vehicle_angle    uid vehicle_lane  vehicle_pos  \
126898 1970-01-01 00:12:04     346.341421  724.0  108934130_0     5.100000   
127110 1970-01-01 00:12:05     346.341421  724.0  108934130_0     7.467381   
127323 1970-01-01 00:12:06     346.341421  724.0  108934130_0    12.183417   
127536 1970-01-01 00:12:07     346.341421  724.0  108934130_0    19.384233   
127748 1970-01-01 00:12:08     346.341421  724.0  108934130_0    28.708013   

        vehicle_slope  vehicle_speed     vehicle_type        lng        lat  
126898            0.0       0.000000  DEFAULT_VEHTYPE  21.889359  43.315400  
127110            0.0       2.367381  DEFAULT_VEHTYPE  21.889354  43.315416  
127323            0.0       4.716036  DEFAULT_VEHTYPE  21.889344  43.315448  
127536            0.0       7.200816  DEFAULT_VEHTYPE  21.889328  43.315498  
127748            0.0       9.323780  DEFAULT_VEHTYPE  21.889308  43.315561

In [23]:
max_dist_traj_map = max_dist_traj.plot_trajectory(zoom=14)
max_dist_traj_map

/usr/local/lib/python3.7/dist-packages/skmob/core/trajectorydataframe.py:571: UserWarning: Only the trajectories of the first 10 users will be plotted. Use the argument `max_users` to specify the desired number of users, or filter the TrajDataFrame.
  start_end_markers=start_end_markers, control_scale=control_scale)
/usr/local/lib/python3.7/dist-packages/skmob/core/trajectorydataframe.py:571: UserWarning: If necessary, trajectories will be down-sampled to have at most `max_points` points. To avoid this, specify `max_points=None`.
  start_end_markers=start_end_markers, control_scale=control_scale)


In [24]:
from skmob.measures.individual import number_of_locations
nl_df = number_of_locations(tdf)
print(nl_df.head())

100%|██████████| 3600/3600 [00:20<00:00, 177.50it/s]

   uid  number_of_locations
0  0.0                   90
1  1.0                   77
2  2.0                  321
3  3.0                  221
4  4.0                  213


In [25]:
from skmob.measures.individual import location_frequency
lf_df = location_frequency(tdf, normalize=False).reset_index()
lf_df.head()

100%|██████████| 3600/3600 [00:13<00:00, 267.96it/s]


uid        lat        lng  location_frequency
0  0.0  43.317005  21.927240                   1
1  0.0  43.326498  21.925260                   1
2  0.0  43.326038  21.925309                   1
3  0.0  43.325838  21.925343                   1
4  0.0  43.325647  21.925381                   1

In [26]:
loc_freq = lf_df[lf_df.location_frequency == lf_df.location_frequency.max()]

In [27]:
loc_freq_map = folium.Map(location=[loc_freq.lat, loc_freq.lng], tiles='Stamen Terrain', zoom_start=14, control_scale=True)
folium.Marker([loc_freq.lat, loc_freq.lng]).add_to(loc_freq_map)

loc_freq_map

## Analysis on AIS dataset

In [28]:
df_ais = pd.read_csv('/content/drive/MyDrive/SIR1/AIS/unipi_ais_dynamic_may2017.csv')

In [29]:
df_ais.head()

t                                          vessel_id  \
0  1494338726000  0fe51bee65c87f2f06f33d5b42fd47dfaf7d99c72336e2...   
1  1494338727000  f4ed004951a6b8cfa3add56e25ddeab78b4cbf02e4f3b5...   
2  1494338727000  0370717aa5e8fa7344ba0118e3ca5ead5e76c7d8c81d99...   
3  1494338728000  e9e095b8cfeea2291ce5e3402db3c2a52b9cd26ccabbfa...   
4  1494338729000  2c257f035198d62b6d074cd0e449265b287bb78be67cf0...   

         lon        lat  heading  speed  course  
0  23.635057  37.943545    219.0    0.0   359.6  
1  23.558020  37.961385    203.0    0.0   354.3  
2  23.587163  37.950803     79.0    6.7    94.1  
3  23.646965  37.932288     90.0    0.0    59.2  
4  23.547978  37.949730    338.0    0.0     NaN

In [30]:
len(df_ais)

4305035

In [31]:
df_ais['t'] = df_ais['t'].values.astype(dtype='datetime64[ms]')
df_ais.head()

t                                          vessel_id  \
0 2017-05-09 14:05:26  0fe51bee65c87f2f06f33d5b42fd47dfaf7d99c72336e2...   
1 2017-05-09 14:05:27  f4ed004951a6b8cfa3add56e25ddeab78b4cbf02e4f3b5...   
2 2017-05-09 14:05:27  0370717aa5e8fa7344ba0118e3ca5ead5e76c7d8c81d99...   
3 2017-05-09 14:05:28  e9e095b8cfeea2291ce5e3402db3c2a52b9cd26ccabbfa...   
4 2017-05-09 14:05:29  2c257f035198d62b6d074cd0e449265b287bb78be67cf0...   

         lon        lat  heading  speed  course  
0  23.635057  37.943545    219.0    0.0   359.6  
1  23.558020  37.961385    203.0    0.0   354.3  
2  23.587163  37.950803     79.0    6.7    94.1  
3  23.646965  37.932288     90.0    0.0    59.2  
4  23.547978  37.949730    338.0    0.0     NaN

In [32]:
num_of_unique_vehicles_ais = df_ais['vessel_id'].nunique()
num_of_unique_vehicles_ais

778

In [33]:
tdf_ais = skmob.TrajDataFrame(df_ais, latitude='lat', longitude='lon', datetime='t', user_id='vessel_id')
tdf_ais.head()

datetime                                                uid  \
0 2017-05-09 14:05:26  0fe51bee65c87f2f06f33d5b42fd47dfaf7d99c72336e2...   
1 2017-05-09 14:05:27  f4ed004951a6b8cfa3add56e25ddeab78b4cbf02e4f3b5...   
2 2017-05-09 14:05:27  0370717aa5e8fa7344ba0118e3ca5ead5e76c7d8c81d99...   
3 2017-05-09 14:05:28  e9e095b8cfeea2291ce5e3402db3c2a52b9cd26ccabbfa...   
4 2017-05-09 14:05:29  2c257f035198d62b6d074cd0e449265b287bb78be67cf0...   

         lng        lat  heading  speed  course  
0  23.635057  37.943545    219.0    0.0   359.6  
1  23.558020  37.961385    203.0    0.0   354.3  
2  23.587163  37.950803     79.0    6.7    94.1  
3  23.646965  37.932288     90.0    0.0    59.2  
4  23.547978  37.949730    338.0    0.0     NaN

In [46]:
map_with_ais_traj = tdf_ais.plot_trajectory(zoom=14, max_users=30)
map_with_ais_traj

/usr/local/lib/python3.7/dist-packages/skmob/core/trajectorydataframe.py:571: UserWarning: If necessary, trajectories will be down-sampled to have at most `max_points` points. To avoid this, specify `max_points=None`.
  start_end_markers=start_end_markers, control_scale=control_scale)


In [35]:
stdf = detection.stay_locations(tdf_ais, stop_radius_factor=0.5, minutes_for_a_stop=20.0, spatial_radius_km=0.2, leaving_time=True)
stdf.head()

datetime                                                uid  \
0 2017-05-31 07:34:33  001680b0d55b053ae6558a0ce257e717dfd188fd98e6c2...   
1 2017-05-09 15:44:33  002351f7584dcb3b6ab87557073727eadd310a71e141d3...   
2 2017-05-10 08:10:44  002351f7584dcb3b6ab87557073727eadd310a71e141d3...   
3 2017-05-10 22:41:48  002351f7584dcb3b6ab87557073727eadd310a71e141d3...   
4 2017-05-11 08:49:31  002351f7584dcb3b6ab87557073727eadd310a71e141d3...   

         lng        lat  heading  speed  course    leaving_datetime  
0  23.649205  37.931038    322.0    0.0   317.3 2017-05-31 20:58:34  
1  23.547683  37.965100    343.0    8.9   342.7 2017-05-10 08:02:15  
2  23.590904  38.027210    259.0    3.9   262.7 2017-05-10 22:41:48  
3  23.584937  38.025511    255.0    6.0   254.8 2017-05-11 07:34:14  
4  23.619832  37.807583    154.0    9.3   153.8 2017-05-19 12:25:25

In [36]:
map_f = tdf_ais.plot_trajectory(max_points=1000, max_users=30, start_end_markers=False)
stdf.plot_stops(map_f=map_f)

/usr/local/lib/python3.7/dist-packages/skmob/core/trajectorydataframe.py:571: UserWarning: If necessary, trajectories will be down-sampled to have at most `max_points` points. To avoid this, specify `max_points=None`.
  start_end_markers=start_end_markers, control_scale=control_scale)
/usr/local/lib/python3.7/dist-packages/skmob/core/trajectorydataframe.py:648: UserWarning: Only the stops of the first 10 users will be plotted. Use the argument `max_users` to specify the desired number of users, or filter the TrajDataFrame.
  popup=popup, control_scale=control_scale)


In [37]:
# Trajectory compression
ctdf_ais = compression.compress(tdf_ais, spatial_radius_km=0.2)
print('Points of the original trajectory:\t%s'%len(tdf_ais))
print('Points of the compressed trajectory:\t%s'%len(ctdf_ais))

Points of the original trajectory:	4305035
Points of the compressed trajectory:	119784


### Measures on AIS dataset

In [38]:
vl_df = visits_per_location(tdf_ais)
vl_df.head()

lat        lng  n_visits
0  37.929667  23.681500     69858
1  37.931000  23.683000     38104
2  37.940038  23.623788     34983
3  37.943000  23.641167     28691
4  37.932833  23.647833     23571

In [39]:
fr_df = frequency_rank(tdf_ais)
fr_df.head()

100%|██████████| 778/778 [00:07<00:00, 103.22it/s]


lat        lng  \
uid                                                                          
001680b0d55b053ae6558a0ce257e717dfd188fd98e6c2c... 0  37.931033  23.649198   
                                                   1  37.931042  23.649195   
                                                   2  37.931028  23.649205   
                                                   3  37.931023  23.649212   
                                                   4  37.931060  23.649167   

                                                      frequency_rank  
uid                                                                   
001680b0d55b053ae6558a0ce257e717dfd188fd98e6c2c... 0               1  
                                                   1               2  
                                                   2               3  
                                                   3               4  
                                                   4               5

In [40]:
from skmob.measures.individual import max_distance_from_home
dh_max = max_distance_from_home(tdf_ais)
dh_max.head()
dh_max.max_distance_from_home.max()

100%|██████████| 778/778 [00:29<00:00, 26.32it/s]


70.17733551478935

In [41]:
from skmob.measures.individual import number_of_locations
nl_df = number_of_locations(tdf_ais)
nl_df.head()

100%|██████████| 778/778 [00:28<00:00, 27.41it/s]


uid  number_of_locations
0  001680b0d55b053ae6558a0ce257e717dfd188fd98e6c2...                  200
1  002351f7584dcb3b6ab87557073727eadd310a71e141d3...                 2666
2  00a0d09a8cb3a714dfc2c75f208f7b570aa9fa86fa57d5...                   14
3  00aceee2b56d4833d9993cb44a0b7455679aea9407efea...                    2
4  00c7725d1ff8ff36fc4091b1aef03261fb1a9e38b11f20...                    1

In [42]:
from skmob.measures.individual import home_location
hl_df = home_location(tdf_ais)
hl_df.head()

100%|██████████| 778/778 [00:05<00:00, 146.11it/s]


uid        lat        lng
0  001680b0d55b053ae6558a0ce257e717dfd188fd98e6c2...  37.931033  23.649198
1  002351f7584dcb3b6ab87557073727eadd310a71e141d3...  38.025412  23.584618
2  00a0d09a8cb3a714dfc2c75f208f7b570aa9fa86fa57d5...  37.902747  23.676073
3  00aceee2b56d4833d9993cb44a0b7455679aea9407efea...  37.908545  23.698775
4  00c7725d1ff8ff36fc4091b1aef03261fb1a9e38b11f20...  37.955260  23.607925

In [43]:
home_loc = hl_df.head(10)
home_loc_map = folium.Map(location=[home_loc.lat.mean(), home_loc.lng.mean()], tiles='Stamen Terrain', zoom_start=14, control_scale=True)

for index, location_info in home_loc.iterrows():
    folium.Marker([location_info["lat"], location_info["lng"]]).add_to(home_loc_map)

In [44]:
home_loc_map

In [45]:
from skmob.measures.collective import visits_per_time_unit
vtu_df = visits_per_time_unit(tdf_ais)
print(vtu_df.head(10))

                     n_visits
datetime                     
2017-05-09 14:00:00     24530
2017-05-09 15:00:00     24654
2017-05-09 16:00:00     26682
2017-05-09 17:00:00     26182
2017-05-09 18:00:00     23836
2017-05-09 19:00:00     22088
2017-05-09 20:00:00     22080
2017-05-09 21:00:00     18538
2017-05-09 22:00:00     18140
2017-05-09 23:00:00     18948
